In [1]:
# from google.colab import drive
# drive.mount('/content/drive')#, force_"remount=True)

Mounted at /content/drive


# Setup

In [2]:
# %cd /content/drive/My\ Drive/TUM/SEM3/Praktikum-XAI/


/content/drive/My Drive/TUM/SEM3/Praktikum-XAI


In [3]:
# !git clone https://github.com/mekladious/Esca_Code
%cd Esca_Code
# !git checkout xai
# !git checkout master

/content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Esca_Code


In [ ]:
# !git clone https://github.com/mekladious/Centrality_Pre_Summ
# %cd Centrality_Pre_Summ
# !git checkout xai

# !git clone https://github.com/mekladious/PreSumm
# %cd PreSumm
# !git checkout -b xai

In [ ]:
# !source ./venv/bin/activate;
%%capture
%pip install -r requirements.txt

### ROUGE FIX



https://stackoverflow.com/questions/45894212/installing-pyrouge-gets-error-in-ubuntu

In [ ]:
# !git clone https://github.com/bheinzerling/pyrouge
# % cd pyrouge 
# !pip install -e .


In [ ]:
# !git clone https://github.com/andersjo/pyrouge.git rouge
!pyrouge_set_rouge_path /content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Esca_Code/rouge/tools/ROUGE-1.5.5/

2022-02-08 16:40:47,564 [MainThread  ] [INFO ]  Set ROUGE home directory to /content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Esca_Code/rouge/tools/ROUGE-1.5.5/.


In [ ]:
# to fix "Can't locate XML/Parser.pm in @INC (you may need to install the XML::Parser module" error
%%capture
!sudo apt-get install libxml-parser-perl

In [ ]:
# %cd rouge/tools/ROUGE-1.5.5/data
# !rm WordNet-2.0.exc.db
# !./WordNet-2.0-Exceptions/buildExeptionDB.pl ./WordNet-2.0-Exceptions ./smart_common_words.txt ./WordNet-2.0.exc.db

In [ ]:
!chmod 777 /content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Esca_Code/rouge/tools/ROUGE-1.5.5/ROUGE-1.5.5.pl

# **ESCA**

In [ ]:
%cd BERT/src

/content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Esca_Code/BERT/src


## **Extractor**

### **Training**

In [ ]:
!python train.py --pairwise -task ext -mode train -bert_data_path ../bert_data \
-ext_dropout 0.1 -model_path ../models_checkpoints/bert_ext -lr 2e-3 \
-visible_gpus 0 -report_every 100 -save_checkpoint_steps 1800 -batch_size 3000 \
-train_steps 10000 -accum_count 2 -log_file ../logs/ext_bert_cnndm.log -use_interval true \
-warmup_steps 10000 -max_pos 512


### Test by ROUGE

In [ ]:
# %%capture
# !pip install seaborn matplotlib


In [ ]:
!python train.py -test_from ../models_checkpoints/bert_ext/model_step_1800.pt \
-task ext -mode test -batch_size 3000 -test_batch_size 500 \
-bert_data_path ../bert_data/cnndm.test.0.bert -log_file ../logs/test_ext_bert_cnndm.log \
-model_path ../models_checkpoints -sep_optim true -use_interval true \
-visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 \
-result_path "../results/cnndm_test_0_bert"


Streaming output truncated to the last 5000 lines.
         0.0417, 0.0417, 0.0417, 0.0417, 0.0417, 0.0417]], device='cuda:0')
batch.src_str [['brendan rodgers has insisted that raheem sterling will not be sold this summer , even if he fails to agree a new long-term contract at anfield .', "but as we 've seen in the past - with luis suarez 's move to barcelona a prime example - that sort of promise is n't always kept .", 'here , sportsmail takes a look at five possible destinations for the england man .', 'raheem sterling , pictured in training on thursday , has attracted interest from a number of big clubs', 'the gunners have a genuine interest in the liverpool wonderkid and believe they have the financial capabilities to pull off a mega-deal .', 'but when push comes to shove , can they emerge victorious in what could turn out to be an auction ?', 'sterling has rejected a contract worth # 100,000-a-week and could look to force a move away from liverpool', "the big question is how woul

### Validate by ROUGE

In [ ]:
!python train.py -task ext -mode validate -batch_size 15000 -control Rel \
-test_batch_size 15000 -bert_data_path ../bert_data \
-log_file ../logs/val_ext_bert_cnndm.log \
-model_path ../models_checkpoints/bert_ext -sep_optim true -use_interval true \
-visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 \
-result_path ../results -test_all 


In [ ]:
# !python train.py -task ext -mode validate -batch_size 15000 -control Rel \
# -test_batch_size 15000 -bert_data_path ../bert_data \
# -log_file ../logs/val_ext_bert_cnndm.log \
# -model_path ../models_checkpoints/presumm -sep_optim true -use_interval true \
# -visible_gpus 0 -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 \
# -result_path ../results -test_all 


[2022-02-05 10:38:07,035 INFO] PPL []


## **Abstractor**

In [ ]:
!python train.py -task abs -mode train -bert_data_path ../bert_data \
-dec_dropout 0.2 -sep_optim true -lr_bert 0.002 -lr_dec 0.2 \
-save_checkpoint_steps 500 -batch_size 140 -train_steps 10000 -report_every 50 \
-accum_count 4 -use_bert_emb true -use_interval true -warmup_steps_bert 20000 \
-warmup_steps_dec 10000 -max_pos 512 -visible_gpus 0 \
-log_file ../logs/abs_bert_cnndm.log


[2022-01-24 00:57:15,166 INFO] Namespace(accum_count=4, alpha=0.6, batch_size=140, beam_size=5, bert_data_path='../bert_data', beta1=0.9, beta2=0.999, block_trigram=True, cal_square=False, control='None', dec_dropout=0.2, dec_ff_size=2048, dec_heads=8, dec_hidden_size=768, dec_layers=6, enc_dropout=0.2, enc_ff_size=512, enc_hidden_size=512, enc_layers=6, encoder='bert', ext_dropout=0.2, ext_ff_size=2048, ext_heads=8, ext_hidden_size=768, ext_layers=1, finetune_bert=True, generator_shard_size=32, gpu_ranks=[0], hybrid_connector=False, hybrid_loss=False, is_debugging=False, label_smoothing=0.1, large=False, load_from_extractive='', log_file='../logs/abs_bert_cnndm.log', lr=1, lr_bert=0.002, lr_dec=0.2, max_grad_norm=0, max_length=150, max_pos=512, max_tgt_len=140, min_length=15, mode='train', model_path='../models/', optim='adam', oracle=False, pairwise=False, param_init=0, param_init_glorot=True, recall_eval=False, report_every=50, report_rouge=True, result_path='../results/cnndm', save

## **Hybrid**

In [ ]:

# -train_from_abstractor ABSTRACTOR_CHECKPOINT_PATH \

In [ ]:
!python train.py \
-train_from_extractor ../models_checkpoints/bert_ext/model_step_1700.pt \
--hybrid_loss -lr 0.002 \
-task hybrid -mode train -model_path=../models_checkpoints/bert_hybrid \
-bert_data_path ../bert_data -ext_dropout 0.1 -visible_gpus 0 -report_every 50 \
-save_checkpoint_steps 500 -batch_size 2000 -train_steps 10000 \
-accum_count 5 -log_file ../logs/hybrid_bert_cnndm.log -use_interval true \
-warmup_steps_bert 10000 -warmup_steps_dec 5000 -max_pos 512 


[2022-01-24 00:56:15,671 INFO] Device ID 0
[2022-01-24 00:56:15,672 INFO] Device cuda
[2022-01-24 00:56:15,747 INFO] Loading checkpoint from ../models_checkpoints/bert_ext/model_step_1700.pt
[2022-01-24 00:56:21,291 INFO] loading configuration file https://s3.amazonaws.com/models.huggingface.co/bert/bert-base-uncased-config.json from cache at ../temp/4dad0251492946e18ac39290fcfe91b89d370fee250efe9521476438fe8ca185.7156163d5fdc189c3016baca0775ffce230789d7fa2a42ef516483e4ca884517
[2022-01-24 00:56:21,295 INFO] Model config {
  "architectures": [
    "BertForMaskedLM"
  ],
  "attention_probs_dropout_prob": 0.1,
  "finetuning_task": null,
  "hidden_act": "gelu",
  "hidden_dropout_prob": 0.1,
  "hidden_size": 768,
  "initializer_range": 0.02,
  "intermediate_size": 3072,
  "layer_norm_eps": 1e-12,
  "max_position_embeddings": 512,
  "model_type": "bert",
  "num_attention_heads": 12,
  "num_hidden_layers": 12,
  "num_labels": 2,
  "output_attentions": false,
  "output_hidden_states": false,


## **Hybrid with PreSumm Ext**

In [ ]:
!python train.py \
-train_from_extractor ../model_checkpoints/presumm/bertext_cnndm_transformer.pt \
# -train_from_abstractor ABSTRACTOR_CHECKPOINT_PATH \
--hybrid_loss -lr 0.002 \
-task hybrid -mode train -model_path=../model_checkpoints \
-data_path ../bert_data -ext_dropout 0.1 -visible_gpus 0 -report_every 50 \
-save_checkpoint_steps 1800 -batch_size 2000 -train_steps 200000 \
-accum_count 5 -log_file ../logs/hybrid_bert_cnndm.log -use_interval true \
-warmup_steps_bert 20000 -warmup_steps_dec 10000 -max_pos 512 

---



---

# **PreSumm**

### **BertExt** ✅

In [ ]:
# !python src/train.py -task ext -mode train -bert_data_path bert_data -ext_dropout 0.1 -model_path models -lr 2e-3 -visible_gpus '0' -report_every 50 -save_checkpoint_steps 5000 -batch_size 3000 -train_steps 40000 -accum_count 2 -log_file logs/ext_bert_cnndm.log -use_interval true -warmup_steps 10000 -max_pos 512


### **TransformerAbs (baseline)**

In [ ]:
# !python src/train.py -mode train -accum_count 5 -batch_size 300 -bert_data_path bert_data \
# -dec_dropout 0.1 -log_file logs/cnndm_baseline.log -lr 0.05 -model_path models \
# -save_checkpoint_steps 2000 -seed 777 -sep_optim false -train_steps 200000 \
# -use_bert_emb true -use_interval true -warmup_steps 8000  -visible_gpus '0' \
# -max_pos 512 -report_every 50 -enc_hidden_size 512  -enc_layers 6 -enc_ff_size 2048 \
# -enc_dropout 0.1 -dec_layers 6 -dec_hidden_size 512 -dec_ff_size 2048 -encoder baseline -task abs


### **BertAbs**

In [ ]:
cd src

/content/drive/MyDrive/TUM/SEM3/Praktikum-XAI/Centrality_Pre_Summ/src


In [ ]:
# !python src/train.py -task abs -mode train -bert_data_path bert_data -dec_dropout 0.2 \
# -model_path models -sep_optim true -lr_bert 0.002 -lr_dec 0.2 -save_checkpoint_steps 2000 \
# -batch_size 140 -train_steps 45000 -report_every 50 -accum_count 5 -use_bert_emb true \
# -use_interval true -warmup_steps_bert 20000 -warmup_steps_dec 10000 -max_pos 512 \
# -visible_gpus '-1' -log_file logs/abs_bert_cnndm.log

# !python train.py --is_debugging -task abs -mode train -bert_data_path ../bert_data -dec_dropout 0.2  -sep_optim true -lr_bert 0.002 -lr_dec 0.2 -save_checkpoint_steps 2000 -batch_size 140 -train_steps 200000 -report_every 50 -accum_count 5 -use_bert_emb true -use_interval true -warmup_steps_bert 20000 -warmup_steps_dec 10000 -max_pos 512 -visible_gpus 0  -log_file ../logs/abs_bert_cnndm.log

# !python src/train.py -task abs -mode train -bert_data_path bert_data -dec_dropout 0.2 -model_path models -sep_optim true -lr_bert 0.002 -lr_dec 0.2 -save_checkpoint_steps 5000 -batch_size 140 -train_steps 40000 -report_every 50 -accum_count 5 -use_bert_emb true -use_interval true -warmup_steps_bert 20000 -warmup_steps_dec 10000 -max_pos 512 -visible_gpus -1 -log_file logs/abs_bert_cnndm.log


### **BertExtAbs**

In [ ]:
# !python src/train.py  -task abs -mode train -bert_data_path bert_data -dec_dropout 0.2  -model_path models -sep_optim true -lr_bert 0.002 -lr_dec 0.2 -save_checkpoint_steps 5000 -batch_size 140 -train_steps 40000 -report_every 50 -accum_count 5 -use_bert_emb true -use_interval true -warmup_steps_bert 20000 -warmup_steps_dec 10000 -max_pos 512 -visible_gpus 0 -log_file logs/abs_ext_bert_cnndm.log -load_from_extractive models/model_step_45000.pt   


# Useful commands

In [ ]:
# !pip install torch==1.8python BERT/src/train.py --pairwise -task ext -mode train -bert_data_path BERT/bert_data -ext_dropout 0.1 -model_path BERT/src/models -lr 2e-3  -visible_gpus '-1' -report_every 100 -save_checkpoint_steps 1000 -batch_size 3000 -train_steps 10000 -accum_count 2 -log_file logs/modeling.log -use_interval true -warmup_steps 10000 -max_pos 512

# !git pull origin esca_presumm
# !python BERT/src/train.py --pairwise -task ext -mode train -bert_data_path BERT/bert_data -ext_dropout 0.1 -model_path BERT/src/models -lr 2e-3  -visible_gpus '0' -report_every 100 -save_checkpoint_steps 1000 -batch_size 3000 -train_steps 10000 -accum_count 2 -log_file logs/modeling.log -use_interval true -warmup_steps 10000 -max_pos 512
# error with datafile 'BERT/bert_data/cnndm.train.62.bert.pt'
# error with datafile 'BERT/bert_data/cnndm.train.1.bert.pt'

# !wget https://developer.nvidia.com/compute/cuda/9.2/Prod/local_installers/cuda-repo-ubuntu1604-9-2-local_9.2.88-1_amd64 -O cuda-repo-ubuntu1604-9-2-local_9.2.88-1_amd64.deb
# !dpkg -i cuda-repo-ubuntu1604-9-2-local_9.2.88-1_amd64.deb
# !apt-key add /var/cuda-repo-9-2-local/7fa2af80.pub
# !apt-get update
# !apt-get install cuda
# !pip install mxnet-cu92

# import torch
# torch.cuda.is_available()
# !nvcc --version
# !nvidia-smi

In [ ]:
# %cd src
# ! python train.py -task abs -mode validate -batch_size 3000 -test_batch_size 500 -bert_data_path bert_data \
# -log_file ../logs/val_abs_bert_cnndm -model_path MODEL_PATH -sep_optim true -use_interval true -visible_gpus 1 \
# -max_pos 512 -max_length 200 -alpha 0.95 -min_length 50 -result_path ../logs/abs_bert_cnndm.log


python3: can't open file 'train.py': [Errno 2] No such file or directory
